In [1]:
import streamlit as st
import pandas as pd
import altair as alt
from vega_datasets import data

alt.data_transformers.disable_max_rows()

/Users/huangbenson/.pyenv/versions/3.7.8/envs/05839-3.7.8/lib/python3.7/site-packages/pandas/compat/__init__.py:97: UserWarning: Could not import the lzma module. Your installed Python is incomplete. Attempting to use lzma compression will result in a RuntimeError.
  warnings.warn(msg)


DataTransformerRegistry.enable('default')

In [34]:
states_mapping = {
        'AK': 'Alaska',
        'AL': 'Alabama',
        'AR': 'Arkansas',
        'AS': 'American Samoa',
        'AZ': 'Arizona',
        'CA': 'California',
        'CO': 'Colorado',
        'CT': 'Connecticut',
        'DC': 'District of Columbia',
        'DE': 'Delaware',
        'FL': 'Florida',
        'GA': 'Georgia',
        'GU': 'Guam',
        'HI': 'Hawaii',
        'IA': 'Iowa',
        'ID': 'Idaho',
        'IL': 'Illinois',
        'IN': 'Indiana',
        'KS': 'Kansas',
        'KY': 'Kentucky',
        'LA': 'Louisiana',
        'MA': 'Massachusetts',
        'MD': 'Maryland',
        'ME': 'Maine',
        'MI': 'Michigan',
        'MN': 'Minnesota',
        'MO': 'Missouri',
        'MP': 'Northern Mariana Islands',
        'MS': 'Mississippi',
        'MT': 'Montana',
        'NA': 'National',
        'NC': 'North Carolina',
        'ND': 'North Dakota',
        'NE': 'Nebraska',
        'NH': 'New Hampshire',
        'NJ': 'New Jersey',
        'NM': 'New Mexico',
        'NV': 'Nevada',
        'NY': 'New York',
        'OH': 'Ohio',
        'OK': 'Oklahoma',
        'OR': 'Oregon',
        'PA': 'Pennsylvania',
        'PR': 'Puerto Rico',
        'RI': 'Rhode Island',
        'SC': 'South Carolina',
        'SD': 'South Dakota',
        'TN': 'Tennessee',
        'TX': 'Texas',
        'UT': 'Utah',
        'VA': 'Virginia',
        'VI': 'Virgin Islands',
        'VT': 'Vermont',
        'WA': 'Washington',
        'WI': 'Wisconsin',
        'WV': 'West Virginia',
        'WY': 'Wyoming'
}

In [31]:
review = None 
business = None 
url = "https://raw.githubusercontent.com/emanuelemassaro/pois/master/indonesia_education.csv"
url = "https://github.com/CMU-IDS-2021/assignment-2-05839-benson/blob/f9f82f7c2b67ffa287789ad4ed713b5b9ccd663b/data/business.json"
def load_data():
#     yelpr_url = "/Users/huangbenson/Downloads/archive/yelp_academic_dataset_review.json"
    yelpb_url = "https://github.com/CMU-IDS-2021/assignment-2-05839-benson/blob/f9f82f7c2b67ffa287789ad4ed713b5b9ccd663b/data/business.json?raw=true"
    
    
    business = pd.read_json(yelpb_url, lines=True)
#     review = pd.read_json(yelpr_url, lines=True, nrows=200000)
    return (business)
    # penguins_url = "https://raw.githubusercontent.com/allisonhorst/palmerpenguins/v0.1.0/inst/extdata/penguins.csv"
business = load_data()

RemoteDisconnected: Remote end closed connection without response

In [128]:
# review_score = review.groupby("business_id").agg({'stars':'mean'})
business_state = business.groupby("state")
business_state_review_count = business_state.agg({'stars':'mean'})
business_state_review_count['state'] = business_state_review_count.index
business_state_review_count


stars state
state                
ABE    4.500000   ABE
AL     2.500000    AL
AZ     4.000000    AZ
BC     3.512574    BC
CA     4.230769    CA
CO     3.774703    CO
DC     5.000000    DC
DE     4.500000    DE
FL     3.554343    FL
GA     3.507822    GA
HI     4.500000    HI
IL     4.000000    IL
KS     2.000000    KS
KY     2.000000    KY
MA     3.618211    MA
ME     3.500000    ME
MI     3.500000    MI
MN     3.500000    MN
NC     2.500000    NC
NH     3.000000    NH
NM     3.500000    NM
NY     5.000000    NY
OH     3.533043    OH
OK     2.500000    OK
ON     3.750000    ON
OR     3.863873    OR
TX     3.846314    TX
VA     2.750000    VA
WA     3.660205    WA
WI     3.500000    WI
WY     1.500000    WY

In [44]:
# add data 
pop = data.population_engineers_hurricanes()

business_state = business.groupby("state")
business_state_review_count = business_state.agg({'stars':'mean'})
business_state_review_count['state'] = business_state_review_count.index
def to_map(abbr):
    if abbr in states_mapping:
        return int(pop[pop.state == states_mapping[abbr]].id.iloc[0])
    else:
        return None
    
business_state_review_count.state = business_state_review_count.state.apply(to_map)
business_state_review_count = business_state_review_count[business_state_review_count.state.notna()]
business_state_review_count.state = business_state_review_count.state.astype("int")
business_state_review_count.reset_index(drop=True, inplace=True)

In [45]:
def EOQ(idd):
    Q = business_state_review_count[business_state_review_count.state == idd].stars
    if Q is not None:
        try: 
            g = Q.iloc[0]
            return g
        except:
            return 0
    else: 
        return 0

pop['stars'] = pop.apply(lambda row: EOQ(row["id"]), axis = 1)

In [47]:
states = alt.topo_feature(data.us_10m.url, feature='states')

# selectionn 
hover = alt.selection_single(on='mouseover',fields=['id'], empty='none')
click = alt.selection_single(on='mouseclick',fields=['id'], empty='none')

# base 
base_chart = (
    alt.Chart(states)
    .mark_geoshape(stroke="black", strokeWidth=0.5, color="white")
    .encode(tooltip=[alt.Tooltip(f"state:N", title="asd")])
)

# other 
background_states = alt.Chart(states).mark_geoshape(
).encode(
#     color='population:Q',
    color=alt.condition(hover, alt.value('red'), 'stars:Q'),
    tooltip=['state:N', 'stars:Q']
).transform_lookup(
    lookup='id',
    from_=alt.LookupData(pop, 'id', list(pop.columns))
).project('albersUsa').properties(
    width=500,
    height=300
).add_selection(hover)


base_chart + background_states

alt.LayerChart(...)

In [120]:
from collections import defaultdict 

attributes = ["RestaurantsTableService", "BikeParking", "WiFi", 
              "BusinessAcceptsCreditCards", "RestaurantsReservations", "WheelchairAccessible", 
             "Caters", "OutdoorSeating", "RestaurantsGoodForGroups", "BusinessAcceptsBitcoin"]

after_attributes = [ "mean_stars", "mean_review_count", "mean_is_open",
    "mean_RestaurantsTableService", "mean_BikeParking", "mean_WiFi",
    "mean_BusinessAcceptsCreditCards", "mean_RestaurantsReservations",
    "mean_WheelchairAccessible", "mean_Caters", "mean_OutdoorSeating", 
    "mean_RestaurantsGoodForGroups", "mean_BusinessAcceptsBitcoin"]


def collect(groupbys):
    # mean(stars), mean(review count), mean(is_open), means(other attributes
    attri_whole = defaultdict(int) 
    for index, row in groupbys.iterrows():
        # simple attributes
        attri_whole["mean_stars"] += row['stars']
        attri_whole["mean_review_count"] += row['review_count']
        attri_whole["mean_is_open"] += row['is_open']
        
        # other attributes 
        attri = row['attributes']
        if attri:
            for k, v in attri.items():
                if k in attributes:
                    if k == "WiFi":
                        if not (v == "'no'" or v == "u'no'"):
                            attri_whole[f"mean_{k}"] += 1
                    else:
                        if v == 'True':
                            attri_whole[f"mean_{k}"] += 1
                        
    
    count = groupbys.shape[0]
    dic = dict(attri_whole)
    lis = []
    for a in after_attributes:
        if a in dic.keys():
            lis.append(dic[a] / count)
        else:
            lis.append(0)

    return pd.Series(lis) 
          
business_state = business.groupby("state").apply(collect)
business_state.columns = after_attributes
business_state["state"] = business_state.index
business_state

mean_stars  mean_review_count  mean_is_open  \
state                                                
ABE      4.500000          14.000000      1.000000   
AL       2.500000          11.000000      0.000000   
AZ       4.000000          27.000000      0.500000   
BC       3.512574          34.818650      0.736154   
CA       4.230769          16.769231      0.923077   
CO       3.774703          43.085679      0.760163   
DC       5.000000          10.000000      1.000000   
DE       4.500000           7.000000      1.000000   
FL       3.554343          49.979276      0.817821   
GA       3.507822          61.505583      0.764179   
HI       4.500000           7.000000      1.000000   
IL       4.000000          84.000000      0.000000   
KS       2.000000          28.000000      1.000000   
KY       2.000000          11.000000      1.000000   
MA       3.618211          55.909058      0.759552   
ME       3.500000          11.000000      1.000000   
MI       3.500000           6.000000      1.000000   
MN       3.500000           6.000000      1.000000   
NC       2.500000          31.000000      1.000000   
NH       3.000000          11.250000      1.000000   
NM       3.500000           5.000000      1.000000   
NY       5.000000           6.000000      1.000000   
OH       3.533043          36.802363      0.805827   
OK       2.500000           6.000000      1.000000   
ON       3.750000           6.000000      1.000000   
OR       3.863873          55.580457      0.747011   
TX       3.846314          59.398285      0.755565   
VA       2.750000          62.500000      1.000000   
WA       3.660205          36.870234      0.825056   
WI       3.500000           7.000000      1.000000   
WY       1.500000           9.000000      1.000000   

       mean_RestaurantsTableService  mean_BikeParking  mean_WiFi  \
state                                                              
ABE                        0.000000          0.000000   0.000000   
AL                         0.000000          1.000000   0.000000   
AZ                         0.000000          0.500000   0.000000   
BC                         0.107122          0.470575   0.279223   
CA                         0.000000          0.538462   0.384615   
CO                         0.057223          0.458724   0.232645   
DC                         0.000000          0.000000   1.000000   
DE                         0.000000          0.000000   0.000000   
FL                         0.093349          0.381385   0.285753   
GA                         0.082255          0.334218   0.254229   
HI                         0.000000          0.000000   0.000000   
IL                         0.000000          0.000000   0.000000   
KS                         0.000000          1.000000   0.000000   
KY                         0.000000          0.000000   0.000000   
MA                         0.061091          0.351522   0.196101   
ME                         0.000000          0.000000   0.000000   
MI                         0.000000          0.000000   0.000000   
MN                         0.000000          1.000000   1.000000   
NC                         0.000000          0.000000   0.000000   
NH                         0.000000          0.000000   0.000000   
NM                         0.000000          0.000000   0.000000   
NY                         0.000000          0.000000   0.000000   
OH                         0.080298          0.375555   0.250666   
OK                         0.000000          0.000000   0.000000   
ON                         0.000000          0.000000   0.000000   
OR                         0.055571          0.442701   0.222085   
TX                         0.040270          0.330325   0.200082   
VA                         0.000000          0.000000   0.000000   
WA                         0.059276          0.392502   0.213393   
WI                         0.000000          1.000000   0.000000   
WY                         0.000000          0.0

In [69]:
# check attributes 
from collections import defaultdict 
attri_whole = defaultdict(list) 
for index, row in business.iterrows():
    # other attributes 
    attri = row['attributes']
    if attri:
        for k, v in attri.items():
            if v not in attri_whole[k]:
                attri_whole[k].append(v)
attri_whole

mean_stars  mean_review_count  mean_is_open  \
state                                                
ABE      4.500000          14.000000      1.000000   
AL       2.500000          11.000000      0.000000   
AZ       4.000000          27.000000      0.500000   
BC       3.512574          34.818650      0.736154   
CA       4.230769          16.769231      0.923077   
CO       3.774703          43.085679      0.760163   
DC       5.000000          10.000000      1.000000   
DE       4.500000           7.000000      1.000000   
FL       3.554343          49.979276      0.817821   
GA       3.507822          61.505583      0.764179   
HI       4.500000           7.000000      1.000000   
IL       4.000000          84.000000      0.000000   
KS       2.000000          28.000000      1.000000   
KY       2.000000          11.000000      1.000000   
MA       3.618211          55.909058      0.759552   
ME       3.500000          11.000000      1.000000   
MI       3.500000           6.000000      1.000000   
MN       3.500000           6.000000      1.000000   
NC       2.500000          31.000000      1.000000   
NH       3.000000          11.250000      1.000000   
NM       3.500000           5.000000      1.000000   
NY       5.000000           6.000000      1.000000   
OH       3.533043          36.802363      0.805827   
OK       2.500000           6.000000      1.000000   
ON       3.750000           6.000000      1.000000   
OR       3.863873          55.580457      0.747011   
TX       3.846314          59.398285      0.755565   
VA       2.750000          62.500000      1.000000   
WA       3.660205          36.870234      0.825056   
WI       3.500000           7.000000      1.000000   
WY       1.500000           9.000000      1.000000   

       mean_RestaurantsTableService  mean_BikeParking  mean_WiFi  \
state                                                              
ABE                        0.000000          0.000000   0.000000   
AL                         0.000000          1.000000   0.000000   
AZ                         0.000000          0.500000   0.000000   
BC                         0.107122          0.470575   0.279223   
CA                         0.000000          0.538462   0.384615   
CO                         0.057223          0.458724   0.232645   
DC                         0.000000          0.000000   1.000000   
DE                         0.000000          0.000000   0.000000   
FL                         0.093349          0.381385   0.285753   
GA                         0.082255          0.334218   0.254229   
HI                         0.000000          0.000000   0.000000   
IL                         0.000000          0.000000   0.000000   
KS                         0.000000          1.000000   0.000000   
KY                         0.000000          0.000000   0.000000   
MA                         0.061091          0.351522   0.196101   
ME                         0.000000          0.000000   0.000000   
MI                         0.000000          0.000000   0.000000   
MN                         0.000000          1.000000   1.000000   
NC                         0.000000          0.000000   0.000000   
NH                         0.000000          0.000000   0.000000   
NM                         0.000000          0.000000   0.000000   
NY                         0.000000          0.000000   0.000000   
OH                         0.080298          0.375555   0.250666   
OK                         0.000000          0.000000   0.000000   
ON                         0.000000          0.000000   0.000000   
OR                         0.055571          0.442701   0.222085   
TX                         0.040270          0.330325   0.200082   
VA                         0.000000          0.000000   0.000000   
WA                         0.059276          0.392502   0.213393   
WI                         0.000000          1.000000   0.000000   
WY                         0.000000          0.0

In [119]:
feature = "OutdoorSeating"
alt.Chart(business_state).mark_bar().encode(
    x=f'mean_{feature}:Q',
    y=alt.Y('state:N', sort='-x')
)

alt.Chart(...)

In [90]:
import altair as alt
from vega_datasets import data

source = data.barley()

alt.Chart(source).mark_bar().encode(
    x='sum(yield):Q',
    y=alt.Y('site:N', sort='-x')
)
source

yield           variety  year             site
0    27.00000         Manchuria  1931  University Farm
1    48.86667         Manchuria  1931           Waseca
2    27.43334         Manchuria  1931           Morris
3    39.93333         Manchuria  1931        Crookston
4    32.96667         Manchuria  1931     Grand Rapids
..        ...               ...   ...              ...
115  58.16667  Wisconsin No. 38  1932           Waseca
116  47.16667  Wisconsin No. 38  1932           Morris
117  35.90000  Wisconsin No. 38  1932        Crookston
118  20.66667  Wisconsin No. 38  1932     Grand Rapids
119  29.33333  Wisconsin No. 38  1932           Duluth

[120 rows x 4 columns]

In [98]:
a = {"1" : 2, "2": 3 }
b = pd.DataFrame([a])
b.reset_index(drop=True, inplace=True)
b

1  2
0  2  3

In [121]:
pd.DataFrame({"Geo Name": ["Angola"], "value": [1]})

Geo Name  value
0   Angola      1

In [122]:
pop

state  id  population  engineers  hurricanes     stars
0                Alabama   1     4863300   0.003422          22  2.500000
1                 Alaska   2      741894   0.001591           0  0.000000
2                Arizona   4     6931071   0.004774           0  4.000000
3               Arkansas   5     2988248   0.002440           0  0.000000
4             California   6    39250017   0.007126           0  4.230769
5               Colorado   8     5540545   0.008088           0  3.774703
6            Connecticut   9     3576452   0.005897          10  0.000000
7               Delaware  10      952065   0.004989           2  4.500000
8   District of Columbia  11      681170   0.011759           0  5.000000
9                Florida  12    20612439   0.003300         110  3.554343
10               Georgia  13    10310371   0.004940          20  3.507822
11                Hawaii  15     1428557   0.001624           0  4.500000
12                 Idaho  16     1683140   0.002971           0  0.000000
13              Illinois  17    12801539   0.004478           0  4.000000
14               Indiana  18     6633053   0.002724           0  0.000000
15                  Iowa  19     3134693   0.003716           0  0.000000
16                Kansas  20     2907289   0.003811           0  2.000000
17              Kentucky  21     4436974   0.002089           0  2.000000
18             Louisiana  22     4681666   0.001177          49  0.000000
19                 Maine  23     1331479   0.002291           6  3.500000
20              Maryland  24     6016447   0.006291           2  0.000000
21         Massachusetts  25     6811779   0.010231          10  3.618211
22              Michigan  26     9928300   0.003877           0  3.500000
23             Minnesota  27     5519952   0.006194           0  3.500000
24           Mississippi  28     2988726   0.000934          15  0.000000
25              Missouri  29     6093000   0.004413           0  0.000000
26               Montana  30     1042520   0.002139           0  0.000000
27              Nebraska  31     1907116   0.005621           0  0.000000
28                Nevada  32     2940058   0.002037           0  0.000000
29         New Hampshire  33     1334795   0.006331           2  3.000000
30            New Jersey  34     8944469   0.007724           2  0.000000
31            New Mexico  35     2081015   0.001884           0  3.500000
32              New York  36    19745289   0.004941          12  5.000000
33        North Carolina  37    10146788   0.004227          46  2.500000
34          North Dakota  38      757952   0.003404           0  0.000000
35                  Ohio  39    11614373   0.004096           0  3.533043
36              Oklahoma  40     3923561   0.002286           0  2.500000
37                Oregon  41     4093465   0.005457           0  3.863873
38          Pennsylvania  42    12784227   0.004237           1  0.000000
39          Rhode Island  44     1056426   0.004581           9  0.000000
40        South Carolina  45     4961119   0.002084          31  0.000000
41          South Dakota  46      865454   0.003085           0  0.000000
42             Tennessee  47     6651194   0.002376           0  0.000000
43                 Texas  48    27862596   0.004320          59  3.846314
44                  Utah  49     3051217   0.006440           0  0.000000
45               Vermont  50      624594   0.004643           0  0.000000
46              Virginia  51     8411808   0.008595          12  2.750000
47            Washington  53     7288000   0.010711           0  3.660205
48         West Virginia  54     1831102   0.001283           0  0.000000
49             Wisconsin  55     5778708   0.004821           0  3.500000
50               Wyoming  56      585501   0.001008           0  1.500000
51           Puerto Rico  72     3411307   0.000774           0  0.000000

In [129]:
	yelpr_url = "/Users/huangbenson/Downloads/archive/yelp_academic_dataset_review.json"
	yelpb_url = "/Users/huangbenson/Downloads/archive/yelp_academic_dataset_business.json"
	business = pd.read_json(yelpb_url, lines=True)
	# review = pd.read_json(yelpr_url, lines=True, nrows=200000)

	# get attributes
	business_state = business.groupby("state")
	business_state = business_state.agg({'stars':'mean'})
	business_state["state"] = business_state.index

	# change state ABBR -> state full name
	def to_full(abbr):
		if abbr in states_mapping:
			return states_mapping[abbr]
		else:
			return None
	business_state.state = business_state.state.apply(to_full)

In [137]:
business

business_id                     name               address  \
0       6iYb2HFDywm3zjuRg0shjw      Oskar Blues Taproom          921 Pearl St   
1       tCbdrRPZA0oiIYSmHG3J0w  Flying Elephants at PDX   7000 NE Airport Way   
2       bvN78flM8NLprQ1a1y5dRg           The Reclaimory    4720 Hawthorne Ave   
3       oaepsyvc0J17qwi8cfrOWg              Great Clips    2566 Enterprise Rd   
4       PE9uqAjdw0E4-8mjGl3wVA        Crossfit Terminus   1046 Memorial Dr SE   
...                        ...                      ...                   ...   
160580  D2mHoIDXx9N8mS1pGoKV9Q       Eleven Oaks Realty                         
160581  bQX-kwVTyZgcdZGEPzce6Q             Webb's Honey    21777 State Rd 520   
160582  wvFZ06nmPmQ2-IVoPqVYLA    Painting with a Twist  2164 S Chickasaw Trl   
160583  GB75wPibj3IjNauaoCxyGA              Havana Cafe        910 NW 14th St   
160584  ngmLL5Y5OT-bYHKU0kKrYA              Zora Grille   1370 E Altamonte Dr   

                     city state postal_code   latitude   longitude  stars  \
0                 Boulder    CO       80302  40.017544 -105.283348    4.0   
1                Portland    OR       97218  45.588906 -122.593331    4.0   
2                Portland    OR       97214  45.511907 -122.613693    4.5   
3             Orange City    FL       32763  28.914482  -81.295979    3.0   
4                 Atlanta    GA       30316  33.747027  -84.353424    4.0   
...                   ...   ...         ...        ...         ...    ...   
160580             Austin    TX       78701  30.272921  -97.744386    4.0   
160581            Orlando    FL       32833  28.499836  -81.047478    4.5   
160582            Orlando    FL       32825  28.511615  -81.270020    5.0   
160583           Portland    OR       97209  45.529647 -122.685153    4.0   
160584  Altamonte Springs    FL       32701  28.663047  -81.346728    4.5   

        review_count  is_open  \
0                 86        1   
1                126        1   
2                 13        1   
3                  8        1   
4                 14        1   
...              ...      ...   
160580             8        1   
160581            18        1   
160582             8        0   
160583            10        1   
160584            82        0   

                                               attributes  \
0       {'RestaurantsTableService': 'True', 'WiFi': 'u...   
1       {'RestaurantsTakeOut': 'True', 'RestaurantsAtt...   
2       {'BusinessAcceptsCreditCards': 'True', 'Restau...   
3       {'RestaurantsPriceRange2': '1', 'BusinessAccep...   
4       {'GoodForKids': 'False', 'BusinessParking': '{...   
...                                                   ...   
160580                                               None   
160581  {'RestaurantsTakeOut': 'True', 'RestaurantsPri...   
160582  {'DogsAllowed': 'False', 'ByAppointmentOnly': ...   
160583  {'RestaurantsTakeOut': 'True', 'RestaurantsDel...   
160584  {'RestaurantsReservations': 'True', 'OutdoorSe...   

                                               categories  \
0       Gastropubs, Food, Beer Gardens, Restaurants, B...   
1       Salad, Soup, Sandwiches, Delis, Restaurants, C...   
2       Antiques, Fashion, Used, Vintage & Consignment...   
3                              Beauty & Spas, Hair Salons   
4       Gyms, Active Life, Interval Training Gyms, Fit...   
...                                                   ...   
160580  Real Estate, Real Estate Services, Home Servic...   
160581      Health Markets, Food, Specialty Food, Grocery   
160582  Arts & Entertainment, Paint & Sip, Art Classes...   
160583              Cuban, Sandwiches, Restaurants, Cafes   
160584  Restaurants, Middle Eastern, Mediterranean, Pe...   

                                                    hours  
0       {'Monday': '11:0-23:0', 'Tuesday': '11:0-23:0'...  
1       {'Monday': '5:0-18:0', 'Tuesday': '5:0-17:0', ...  
2       {'Thursday': '11:0-18:0', 'Friday': '11:0-18:0...  
3                 

In [11]:
from uszipcode import SearchEngine
search = SearchEngine() # set simple_zipcode=False to use rich info database
def EOQ(idd):
    zipcode = search.by_zipcode(str(idd))
    if zipcode:
        return zipcode.to_dict()["county"]
    else:
        return None 

business['county'] = business.apply(lambda row: EOQ(row["postal_code"]), axis = 1)

In [12]:
business[business.state_from_zip.notnull()].shape[0]

143080

In [14]:
business

business_id                     name               address  \
0       6iYb2HFDywm3zjuRg0shjw      Oskar Blues Taproom          921 Pearl St   
1       tCbdrRPZA0oiIYSmHG3J0w  Flying Elephants at PDX   7000 NE Airport Way   
2       bvN78flM8NLprQ1a1y5dRg           The Reclaimory    4720 Hawthorne Ave   
3       oaepsyvc0J17qwi8cfrOWg              Great Clips    2566 Enterprise Rd   
4       PE9uqAjdw0E4-8mjGl3wVA        Crossfit Terminus   1046 Memorial Dr SE   
...                        ...                      ...                   ...   
160580  D2mHoIDXx9N8mS1pGoKV9Q       Eleven Oaks Realty                         
160581  bQX-kwVTyZgcdZGEPzce6Q             Webb's Honey    21777 State Rd 520   
160582  wvFZ06nmPmQ2-IVoPqVYLA    Painting with a Twist  2164 S Chickasaw Trl   
160583  GB75wPibj3IjNauaoCxyGA              Havana Cafe        910 NW 14th St   
160584  ngmLL5Y5OT-bYHKU0kKrYA              Zora Grille   1370 E Altamonte Dr   

                     city state postal_code   latitude   longitude  stars  \
0                 Boulder    CO       80302  40.017544 -105.283348    4.0   
1                Portland    OR       97218  45.588906 -122.593331    4.0   
2                Portland    OR       97214  45.511907 -122.613693    4.5   
3             Orange City    FL       32763  28.914482  -81.295979    3.0   
4                 Atlanta    GA       30316  33.747027  -84.353424    4.0   
...                   ...   ...         ...        ...         ...    ...   
160580             Austin    TX       78701  30.272921  -97.744386    4.0   
160581            Orlando    FL       32833  28.499836  -81.047478    4.5   
160582            Orlando    FL       32825  28.511615  -81.270020    5.0   
160583           Portland    OR       97209  45.529647 -122.685153    4.0   
160584  Altamonte Springs    FL       32701  28.663047  -81.346728    4.5   

        review_count  is_open  \
0                 86        1   
1                126        1   
2                 13        1   
3                  8        1   
4                 14        1   
...              ...      ...   
160580             8        1   
160581            18        1   
160582             8        0   
160583            10        1   
160584            82        0   

                                               attributes  \
0       {'RestaurantsTableService': 'True', 'WiFi': 'u...   
1       {'RestaurantsTakeOut': 'True', 'RestaurantsAtt...   
2       {'BusinessAcceptsCreditCards': 'True', 'Restau...   
3       {'RestaurantsPriceRange2': '1', 'BusinessAccep...   
4       {'GoodForKids': 'False', 'BusinessParking': '{...   
...                                                   ...   
160580                                               None   
160581  {'RestaurantsTakeOut': 'True', 'RestaurantsPri...   
160582  {'DogsAllowed': 'False', 'ByAppointmentOnly': ...   
160583  {'RestaurantsTakeOut': 'True', 'RestaurantsDel...   
160584  {'RestaurantsReservations': 'True', 'OutdoorSe...   

                                               categories  \
0       Gastropubs, Food, Beer Gardens, Restaurants, B...   
1       Salad, Soup, Sandwiches, Delis, Restaurants, C...   
2       Antiques, Fashion, Used, Vintage & Consignment...   
3                              Beauty & Spas, Hair Salons   
4       Gyms, Active Life, Interval Training Gyms, Fit...   
...                                                   ...   
160580  Real Estate, Real Estate Services, Home Servic...   
160581      Health Markets, Food, Specialty Food, Grocery   
160582  Arts & Entertainment, Paint & Sip, Art Classes...   
160583              Cuban, Sandwiches, Restaurants, Cafes   
160584  Restaurants, Middle Eastern, Mediterranean, Pe...   

                                                    hours    state_from_zip  
0       {'Monday': '11:0-23:0', 'Tuesday': '11:0-23:0'...    Boulder County  
1       {'Monday': '5:0-18:0', 'Tuesday': '5:0-17:0', ...  Multnomah County  
2       {'Thursday': '11

In [22]:
business_county = business.groupby("state_from_zip").apply(collect)

In [24]:

	business_county.columns = after_attributes
	business_county["county"] = business_county.index

In [26]:
	def to_abbr(abbr):
		if abbr:
			return abbr.split(" County")[0]
		else:
			return None
	business_county.county = business_county.county.apply(to_abbr)
	business_county = business_county[business_county.county.notnull()]
	business_county.reset_index(drop=True, inplace=True)

In [8]:
print(pd.__version__)

1.2.3


In [2]:
import altair as alt
import pandas as pd

df = pd.DataFrame({
    'gg1': [1, 2, 3, 4],
    "gg2": ['A', 'B', 'C', 'D'],
    'color': ['W', 'X', 'Y', 'Z'],
})

hover = alt.selection_single(fields=['gg2'], on='mousedown', nearest=True)

alt.Chart(df).mark_bar().encode(
    x='gg1',
    y="gg2",
    color='color',
    opacity=alt.condition(hover, alt.value(1.0), alt.value(0.3))
).add_selection(hover)

alt.Chart(...)

In [3]:
	yelpr_url = "/Users/huangbenson/Downloads/archive/yelp_academic_dataset_review.json"
	review = pd.read_json(yelpr_url, lines=True, nrows=200000)

In [13]:
	hist = alt.Chart(business).mark_bar().encode(
		y='name:N',
		x=f'{}:N'
	)

alt.Chart(...)

In [37]:
!pip install --upgrade pandas

     |████████████████████████████████| 10.4 MB 36.7 MB/s eta 0:00:01
  Attempting uninstall: pandas
    Found existing installation: pandas 1.0.5
    Uninstalling pandas-1.0.5:
      Successfully uninstalled pandas-1.0.5


In [3]:
import altair as alt
from vega_datasets import data
import pandas as pd

source = data.stocks()

def timestamp(t):
  return pd.to_datetime(t).timestamp() * 1000

slider = alt.binding_range(
    step=30 * 24 * 60 * 60 * 1000, # 30 days in milliseconds
    min=timestamp(min(source['date'])),
    max=timestamp(max(source['date'])))

select_date = alt.selection_single(
    fields=['date'],
    bind=slider,
    init={'date': timestamp(min(source['date']))},
    name='slider')

alt.Chart(source).mark_bar().encode(
    x='symbol',
    y='price',
).add_selection(select_date).transform_filter(
    "(year(datum.date) == year(slider.date[0])) && "
    "(month(datum.date) == month(slider.date[0]))"
)

alt.Chart(...)

In [35]:

def get_data():
	# get data
	yelpb_url = "/Users/huangbenson/Downloads/archive/yelp_academic_dataset_business.json"
	business = pd.read_json(yelpb_url, lines=True)

	# get other attributes
	from collections import defaultdict
	q_attributes = ["stars", "review_count"]
	attributes = ["RestaurantsTableService", "BikeParking", "WiFi",
				  "BusinessAcceptsCreditCards", "RestaurantsReservations", "WheelchairAccessible",
				  "Caters", "OutdoorSeating", "RestaurantsGoodForGroups", "BusinessAcceptsBitcoin"]

	after_attributes = [ "mean_stars", "mean_review_count", "mean_is_open",
						 "mean_RestaurantsTableService", "mean_BikeParking", "mean_WiFi",
						 "mean_BusinessAcceptsCreditCards", "mean_RestaurantsReservations",
						 "mean_WheelchairAccessible", "mean_Caters", "mean_OutdoorSeating",
						 "mean_RestaurantsGoodForGroups", "mean_BusinessAcceptsBitcoin",
						 "max_stars", "max_review_count",
						 "min_stars", "min_review_count"]

	def collect(groupbys):
		# all methods
		attri_whole = defaultdict(int)
		methods = ["max", "min"]
		for m in methods:
			for a in q_attributes:
				if m == "max":
					attri_whole[f"{m}_{a}"] = -1
				else:
					attri_whole[f"{m}_{a}"] = 1e9

		# mean(stars), mean(review count), mean(is_open), means(other attributes
		for index, row in groupbys.iterrows():
			# simple attributes
			attri_whole["mean_stars"] += row['stars']
			attri_whole["mean_review_count"] += row['review_count']
			attri_whole["mean_is_open"] += row['is_open']

			attri_whole["max_stars"] = row["stars"] if row["stars"] > attri_whole["max_stars"] else attri_whole["max_stars"]
			attri_whole["max_review_count"] = row["review_count"] if row["review_count"] > attri_whole["max_review_count"] else attri_whole["max_review_count"]

			attri_whole["min_stars"] = row['stars'] if row["stars"] < attri_whole["min_stars"] else attri_whole["min_stars"]
			attri_whole["min_review_count"] = row['review_count'] if row["review_count"] < attri_whole["min_review_count"] else attri_whole["min_review_count"]


			# other attributes
			attri = row['attributes']
			if attri:
				for k, v in attri.items():
					if k in attributes:
						if k == "WiFi":
							if not (v == "'no'" or v == "u'no'"):
								attri_whole[f"mean_{k}"] += 1
						else:
							if v == 'True':
								attri_whole[f"mean_{k}"] += 1


		count = groupbys.shape[0]
		dic = dict(attri_whole)
		lis = []
		for a in after_attributes:
			if a in dic.keys():
				if a.startswith("mean"):
					lis.append(dic[a] / count)
				else:
					lis.append(dic[a])
			else:
				lis.append(0)

		return pd.Series(lis)

	# get state average
	business_state = business.groupby("state").apply(collect)
	business_state.columns = after_attributes
	business_state["state"] = business_state.index

	# change state ABBR -> state full name
	def to_full(abbr):
		if abbr in states_mapping:
			return states_mapping[abbr]
		else:
			return None
	business_state.state = business_state.state.apply(to_full)
	business_state = business_state[business_state.state.notnull()]
	business_state.reset_index(drop=True, inplace=True)

	# get county from zipcode
	from uszipcode import SearchEngine
	search = SearchEngine() # set simple_zipcode=False to use rich info database
	def EOQ(idd):
		zipcode = search.by_zipcode(str(idd))
		if zipcode:
			return zipcode.to_dict()["county"]
		else:
			return None
	business['county'] = business.apply(lambda row: EOQ(row["postal_code"]), axis=1)

	# get county average
	business_county = business.groupby("county").apply(collect)
	business_county.columns = after_attributes
	business_county["county"] = business_county.index

	# change state ABBR -> state full name
	def to_abbr(abbr):
		if abbr:
			return abbr.split(" County")[0]
		else:
			return None
	business_county.county = business_county.county.apply(to_abbr)
	business_county = business_county[business_county.county.notnull()]
	business_county.reset_index(drop=True, inplace=True)

	# review data
	# yelpr_url = "/Users/huangbenson/Downloads/archive/yelp_academic_dataset_review.json"
	# review = pd.read_json(yelpr_url, lines=True, nrows=200000)

	return business, business_state, business_county
business, business_state, business_county = get_data()

In [6]:
states_mapping = {
	'AK': 'Alaska',
	'AL': 'Alabama',
	'AR': 'Arkansas',
	'AS': 'American Samoa',
	'AZ': 'Arizona',
	'CA': 'California',
	'CO': 'Colorado',
	'CT': 'Connecticut',
	'DC': 'District of Columbia',
	'DE': 'Delaware',
	'FL': 'Florida',
	'GA': 'Georgia',
	'GU': 'Guam',
	'HI': 'Hawaii',
	'IA': 'Iowa',
	'ID': 'Idaho',
	'IL': 'Illinois',
	'IN': 'Indiana',
	'KS': 'Kansas',
	'KY': 'Kentucky',
	'LA': 'Louisiana',
	'MA': 'Massachusetts',
	'MD': 'Maryland',
	'ME': 'Maine',
	'MI': 'Michigan',
	'MN': 'Minnesota',
	'MO': 'Missouri',
	'MP': 'Northern Mariana Islands',
	'MS': 'Mississippi',
	'MT': 'Montana',
	'NA': 'National',
	'NC': 'North Carolina',
	'ND': 'North Dakota',
	'NE': 'Nebraska',
	'NH': 'New Hampshire',
	'NJ': 'New Jersey',
	'NM': 'New Mexico',
	'NV': 'Nevada',
	'NY': 'New York',
	'OH': 'Ohio',
	'OK': 'Oklahoma',
	'OR': 'Oregon',
	'PA': 'Pennsylvania',
	'PR': 'Puerto Rico',
	'RI': 'Rhode Island',
	'SC': 'South Carolina',
	'SD': 'South Dakota',
	'TN': 'Tennessee',
	'TX': 'Texas',
	'UT': 'Utah',
	'VA': 'Virginia',
	'VI': 'Virgin Islands',
	'VT': 'Vermont',
	'WA': 'Washington',
	'WI': 'Wisconsin',
	'WV': 'West Virginia',
	'WY': 'Wyoming'
}

In [67]:
property_title = "state"
data = business_state
method = "mean"
feature = "stars"
display_method = ""

hover = alt.selection_single(on='mouseover', fields=[f'{property_title}'], nearest=True)
highlight = alt.selection_single()
click = alt.selection_single(on='mousedown', fields=[f'{property_title}'])

bar_chart = alt.Chart(data).mark_bar().encode(
    x=f'{method}_{feature}:Q',
    y=alt.Y(f'{property_title}:N', sort='-x'),
    color=alt.condition(highlight, alt.value('red'), alt.value('lightgray')),
    opacity=alt.condition(hover, alt.value(1.0), alt.value(0.3)),
    tooltip=[
        alt.Tooltip(f"{property_title}:N", title=f"{property_title}"),
        alt.Tooltip(f"{method}_{feature}:Q", title=f"{method} of {feature}{display_method}", format=".2~f"),
    ],
).add_selection(hover, click, highlight
).interactive()


hist_chart = alt.Chart(business_state_forshow).mark_point().encode(
    y='stars_x:Q',
    x='name:N',
    tooltip=[
        alt.Tooltip(f"name:N", title=f"name"),
        alt.Tooltip(f"text:N", title=f"review"),
        alt.Tooltip(f"date:N", title=f"date"),
    ],
).transform_filter(click).interactive()

bar_chart | hist_chart

alt.HConcatChart(...)

In [47]:
review

In [27]:
	business_state_forshow = business_state_forshow.merge(review, on="business_id", how='left' )

In [69]:
alt.__version__

'4.1.0'

In [ ]:
# change state ABBR -> state full name
def to_full(abbr):
    if abbr in states_mapping:
        return states_mapping[abbr]
    else:
        return None
business.state = business.state.apply(to_full)
business = business[business.state.notnull()]

In [29]:
def collect(groupbys):
    return groupbys.iloc[:10]
business_state_forshow = business.groupby("state").apply(collect)
business_state_forshow = business_state_forshow.reset_index(level=0, drop=True)
business_state_forshow = business_state_forshow.merge(review, on="business_id", how='left' )
business_state_forshow

def collect(groupbys):
    return groupbys.iloc[:10]
business_county_forshow = business.groupby("county").apply(collect)
business_county_forshow = business_county_forshow.reset_index(level=0, drop=True)
business_county_forshow = business_county_forshow.merge(review, on="business_id", how='left' )
business_county_forshow

business_id                      name  \
0     AhYrutNLVhMDPIWHLUeJNg     Barnie's Coffee & Tea   
1     AhYrutNLVhMDPIWHLUeJNg     Barnie's Coffee & Tea   
2     AhYrutNLVhMDPIWHLUeJNg     Barnie's Coffee & Tea   
3     AhYrutNLVhMDPIWHLUeJNg     Barnie's Coffee & Tea   
4     AhYrutNLVhMDPIWHLUeJNg     Barnie's Coffee & Tea   
...                      ...                       ...   
4850  wbSbtnJMZaz5D_lI-rOSww  Volente Beach Water Park   
4851  wbSbtnJMZaz5D_lI-rOSww  Volente Beach Water Park   
4852  OKPtcundSL2TGtaX4ne8HQ                 Starbucks   
4853  agNH0ocvWMogOlpubWV2qQ               Liz Vequist   
4854  JtJl9urNsACtPzE8PHDb7A       Real Deal Van Lines   

                       address         city state postal_code   latitude  \
0     5750 S W 75th Ct, Ste 60  Gainesville    FL       32608  28.597448   
1     5750 S W 75th Ct, Ste 60  Gainesville    FL       32608  28.597448   
2     5750 S W 75th Ct, Ste 60  Gainesville    FL       32608  28.597448   
3     5750 S W 75th Ct, Ste 60  Gainesville    FL       32608  28.597448   
4     5750 S W 75th Ct, Ste 60  Gainesville    FL       32608  28.597448   
...                        ...          ...   ...         ...        ...   
4850             16107 Fm 2769      Leander    TX       78641  30.441502   
4851             16107 Fm 2769      Leander    TX       78641  30.441502   
4852             5145 N Fm 620       Austin    TX       75783  30.389149   
4853                              Worcester    MA       01604  42.372484   
4854                             Leominster    MA       01453  42.483966   

      longitude  stars_x  review_count  ...             county Unnamed: 0  \
0    -81.350797      4.0            21  ...     Alachua County    32278.0   
1    -81.350797      4.0            21  ...     Alachua County    34758.0   
2    -81.350797      4.0            21  ...     Alachua County    93226.0   
3    -81.350797      4.0            21  ...     Alachua County   148150.0   
4    -81.350797      4.0            21  ...     Alachua County   152752.0   
...         ...      ...           ...  ...                ...        ...   
4850 -97.912603      3.5            44  ...  Williamson County   291477.0   
4851 -97.912603      3.5            44  ...  Williamson County   293324.0   
4852 -97.883809      2.0             6  ...        Wood County        NaN   
4853 -71.099597      5.0             8  ...   Worcester County        NaN   
4854 -71.312449      3.0            73  ...   Worcester County        NaN   

                   review_id                 user_id stars_y  useful funny  \
0     pOgtpjYkd5biugPzgnmI5w  bYedMsts8md9933Zu32CQg     4.0     0.0   0.0   
1     l9EMyPIo8EZyrJAp2bv4sQ  w3ziyp4Eg6oLbKvCwOss_A     4.0     0.0   0.0   
2     cpILPalUDnS5cTGtm5WCvA  IJ4DJH1r44TidJ47E6HDJg     4.0     1.0   0.0   
3     USf-9WtMWHebYSl6IakQPg  R-4GCAMeX5_MBxD0YFEpEQ     5.0     1.0   1.0   
4     AsgkFQ5ZUaPPH99Fec6kqQ  8f02zYozA8ckSjwZx8tZJA     5.0     2.0   0.0   
...                      ...                     ...     ...     ...   ...   
4850  1INyW9_jdQuBIt4gf0yUnQ  hxaKGKg62WtYmmadTQ5fcg     5.0     2.0   0.0   
4851  xgbWAsv6nSaNG-3ZPjiBvA  FrLHvHG8cvPc4GGijIvenA     1.0    20.0  12.0   
4852                     NaN                     NaN     NaN     NaN   NaN   
4853                     NaN                     NaN     NaN     NaN   NaN   
4854                     NaN                     NaN     NaN     NaN   NaN   

     cool                                               text  \
0     0.0  The coffee is good. The espresso and cappuccin...   
1     0.0  I am glad for a place with organic coffees and...   
2     0.0  It is a very nice place. The cookies are wonde...   
3     0.0  This coffee shop is such a nice breather from ...   
4     0.0  I love the coffee here.  It's better than Star...   
...   ...                                                ...   
4850  1.0  My whole family loved this place we have 2 2 y...   
4851  2.0  Do you enjoy feeling l

In [48]:
def get_data():
	# get data
	yelpb_url = "../data/business.json"
	business = pd.read_json(yelpb_url, lines=True)

	# get other attributes
	from collections import defaultdict
	q_attributes = ["stars", "review_count"]
	attributes = ["RestaurantsTableService", "BikeParking", "WiFi",
				  "BusinessAcceptsCreditCards", "RestaurantsReservations", "WheelchairAccessible",
				  "Caters", "OutdoorSeating", "RestaurantsGoodForGroups", "BusinessAcceptsBitcoin"]

	after_attributes = [ "mean_stars", "mean_review_count", "mean_is_open",
						 "mean_RestaurantsTableService", "mean_BikeParking", "mean_WiFi",
						 "mean_BusinessAcceptsCreditCards", "mean_RestaurantsReservations",
						 "mean_WheelchairAccessible", "mean_Caters", "mean_OutdoorSeating",
						 "mean_RestaurantsGoodForGroups", "mean_BusinessAcceptsBitcoin",
						 "max_stars", "max_review_count",
						 "min_stars", "min_review_count"]

	def collect(groupbys):
		# all methods
		attri_whole = defaultdict(int)
		methods = ["max", "min"]
		for m in methods:
			for a in q_attributes:
				if m == "max":
					attri_whole[f"{m}_{a}"] = -1
				else:
					attri_whole[f"{m}_{a}"] = 1e9

		# mean(stars), mean(review count), mean(is_open), means(other attributes
		for index, row in groupbys.iterrows():
			# simple attributes
			attri_whole["mean_stars"] += row['stars']
			attri_whole["mean_review_count"] += row['review_count']
			attri_whole["mean_is_open"] += row['is_open']

			attri_whole["max_stars"] = row["stars"] if row["stars"] > attri_whole["max_stars"] else attri_whole["max_stars"]
			attri_whole["max_review_count"] = row["review_count"] if row["review_count"] > attri_whole["max_review_count"] else attri_whole["max_review_count"]

			attri_whole["min_stars"] = row['stars'] if row["stars"] < attri_whole["min_stars"] else attri_whole["min_stars"]
			attri_whole["min_review_count"] = row['review_count'] if row["review_count"] < attri_whole["min_review_count"] else attri_whole["min_review_count"]


			# other attributes
			attri = row['attributes']
			if attri:
				for k, v in attri.items():
					if k in attributes:
						if k == "WiFi":
							if not (v == "'no'" or v == "u'no'"):
								attri_whole[f"mean_{k}"] += 1
						else:
							if v == 'True':
								attri_whole[f"mean_{k}"] += 1


		count = groupbys.shape[0]
		dic = dict(attri_whole)
		lis = []
		for a in after_attributes:
			if a in dic.keys():
				if a.startswith("mean"):
					lis.append(dic[a] / count)
				else:
					lis.append(dic[a])
			else:
				lis.append(0)

		return pd.Series(lis)

	# change state ABBR -> state full name
	def to_full(abbr):
		if abbr in states_mapping:
			return states_mapping[abbr]
		else:
			return None
	business.state = business.state.apply(to_full)
	business = business[business.state.notnull()]

	# get county from zipcode
	from uszipcode import SearchEngine
	search = SearchEngine() # set simple_zipcode=False to use rich info database
	def EOQ(idd):
		zipcode = search.by_zipcode(str(idd))
		if zipcode:
			return zipcode.to_dict()["county"]
		else:
			return None
	business['county'] = business.apply(lambda row: EOQ(row["postal_code"]), axis=1)
	
	# change state ABBR -> state full name
	def to_abbr(abbr):
		if abbr:
			return abbr.split(" County")[0]
		else:
			return None
	business.county = business.county.apply(to_abbr)
	business = business[business.county.notnull()]
	
	# get state average
	business_state = business.groupby("state").apply(collect)
	business_state.columns = after_attributes
	business_state["state"] = business_state.index

	# get county average
	business_county = business.groupby("county").apply(collect)
	business_county.columns = after_attributes
	business_county["county"] = business_county.index


	# review data
	yelpr_url = "../data/review.csv"
	review = pd.read_csv(yelpr_url)

	# get view joined data
	def collect(groupbys):
		return groupbys.iloc[:10]
	business_state_forshow = business.groupby("state").apply(collect)
	business_state_forshow = business_state_forshow.reset_index(level=0, drop=True)
	business_state_forshow = business_state_forshow.merge(review, on="business_id", how='left' )

	def collect(groupbys):
		return groupbys.iloc[:10]
	business_county_forshow = business.groupby("county").apply(collect)
	business_county_forshow = business_county_forshow.reset_index(level=0, drop=True)
	business_county_forshow = business_county_forshow.merge(review, on="business_id", how='left' )

	return business, business_state, business_county, business_state_forshow, business_county_forshow
business, business_state, business_county, business_state_forshow, business_county_forshow = get_data()


In [77]:
business_state.to_csv("business_state.csv")

In [79]:
business_county.to_csv("business_county.csv")
business_state_forshow.to_csv("business_state_forshow.csv")
business_county_forshow.to_csv("business_county_forshow.csv")

In [83]:
business_state = pd.read_csv("https://raw.githubusercontent.com/SteinsGate9/assignemnt2/main/data/business_county.csv")

URLError: <urlopen error [Errno 61] Connection refused>

In [65]:
def get_data():
	# get data
	yelpb_url = "./data/business.json"
	business = pd.read_json(yelpb_url, lines=True)

	# get other attributes
	from collections import defaultdict
	q_attributes = ["stars", "review_count"]
	attributes = ["RestaurantsTableService", "BikeParking", "WiFi",
				  "BusinessAcceptsCreditCards", "RestaurantsReservations", "WheelchairAccessible",
				  "Caters", "OutdoorSeating", "RestaurantsGoodForGroups", "BusinessAcceptsBitcoin"]

	after_attributes = [ "mean_stars", "mean_review_count", "mean_is_open",
						 "mean_RestaurantsTableService", "mean_BikeParking", "mean_WiFi",
						 "mean_BusinessAcceptsCreditCards", "mean_RestaurantsReservations",
						 "mean_WheelchairAccessible", "mean_Caters", "mean_OutdoorSeating",
						 "mean_RestaurantsGoodForGroups", "mean_BusinessAcceptsBitcoin",
						 "max_stars", "max_review_count",
						 "min_stars", "min_review_count"]

	def collect(groupbys):
		# all methods
		attri_whole = defaultdict(int)
		methods = ["max", "min"]
		for m in methods:
			for a in q_attributes:
				if m == "max":
					attri_whole[f"{m}_{a}"] = -1
				else:
					attri_whole[f"{m}_{a}"] = 1e9

		# mean(stars), mean(review count), mean(is_open), means(other attributes
		for index, row in groupbys.iterrows():
			# simple attributes
			attri_whole["mean_stars"] += row['stars']
			attri_whole["mean_review_count"] += row['review_count']
			attri_whole["mean_is_open"] += row['is_open']

			attri_whole["max_stars"] = row["stars"] if row["stars"] > attri_whole["max_stars"] else attri_whole["max_stars"]
			attri_whole["max_review_count"] = row["review_count"] if row["review_count"] > attri_whole["max_review_count"] else attri_whole["max_review_count"]

			attri_whole["min_stars"] = row['stars'] if row["stars"] < attri_whole["min_stars"] else attri_whole["min_stars"]
			attri_whole["min_review_count"] = row['review_count'] if row["review_count"] < attri_whole["min_review_count"] else attri_whole["min_review_count"]


			# other attributes
			attri = row['attributes']
			if attri:
				for k, v in attri.items():
					if k in attributes:
						if k == "WiFi":
							if not (v == "'no'" or v == "u'no'"):
								attri_whole[f"mean_{k}"] += 1
						else:
							if v == 'True':
								attri_whole[f"mean_{k}"] += 1


		count = groupbys.shape[0]
		dic = dict(attri_whole)
		lis = []
		for a in after_attributes:
			if a in dic.keys():
				if a.startswith("mean"):
					lis.append(dic[a] / count)
				else:
					lis.append(dic[a])
			else:
				lis.append(0)

		return pd.Series(lis)

	# change state ABBR -> state full name
	def to_full(abbr):
		if abbr in states_mapping:
			return states_mapping[abbr]
		else:
			return None
	business.state = business.state.apply(to_full)
	business = business[business.state.notnull()]

	# get county from zipcode
	from uszipcode import SearchEngine
	search = SearchEngine() # set simple_zipcode=False to use rich info database
	def EOQ(idd):
		zipcode = search.by_zipcode(str(idd))
		if zipcode:
			return zipcode.to_dict()["county"]
		else:
			return None
	business['county'] = business.apply(lambda row: EOQ(row["postal_code"]), axis=1)
	
	# change state ABBR -> state full name
	def to_abbr(abbr):
		if abbr:
			return abbr.split(" County")[0]
		else:
			return None
	business.county = business.county.apply(to_abbr)
	business = business[business.county.notnull()]
	
	# get state average
	business_state = business.groupby("state").apply(collect)
	business_state.columns = after_attributes
	business_state["state"] = business_state.index

	# get county average
	business_county = business.groupby("county").apply(collect)
	business_county.columns = after_attributes
	business_county["county"] = business_county.index


	# review data
	yelpr_url = "./data/review.csv"
	review = pd.read_csv(yelpr_url)

	# get view joined data
	def collect(groupbys):
		return groupbys.iloc[:10]
	business_state_forshow = business.groupby("state").apply(collect)
	business_state_forshow = business_state_forshow.reset_index(level=0, drop=True)
	business_state_forshow = business_state_forshow.merge(review, on="business_id", how='left' )

	def collect(groupbys):
		return groupbys.iloc[:10]
	business_county_forshow = business.groupby("county").apply(collect)
	business_county_forshow = business_county_forshow.reset_index(level=0, drop=True)
	business_county_forshow = business_county_forshow.merge(review, on="business_id", how='left' )

	return business, business_state, business_county, business_state_forshow, business_county_forshow

business, business_state, business_county, business_state_forshow, business_county_forshow = get_data()


In [66]:
business

business_id                     name               address  \
0       6iYb2HFDywm3zjuRg0shjw      Oskar Blues Taproom          921 Pearl St   
1       tCbdrRPZA0oiIYSmHG3J0w  Flying Elephants at PDX   7000 NE Airport Way   
2       bvN78flM8NLprQ1a1y5dRg           The Reclaimory    4720 Hawthorne Ave   
3       oaepsyvc0J17qwi8cfrOWg              Great Clips    2566 Enterprise Rd   
4       PE9uqAjdw0E4-8mjGl3wVA        Crossfit Terminus   1046 Memorial Dr SE   
...                        ...                      ...                   ...   
160580  D2mHoIDXx9N8mS1pGoKV9Q       Eleven Oaks Realty                         
160581  bQX-kwVTyZgcdZGEPzce6Q             Webb's Honey    21777 State Rd 520   
160582  wvFZ06nmPmQ2-IVoPqVYLA    Painting with a Twist  2164 S Chickasaw Trl   
160583  GB75wPibj3IjNauaoCxyGA              Havana Cafe        910 NW 14th St   
160584  ngmLL5Y5OT-bYHKU0kKrYA              Zora Grille   1370 E Altamonte Dr   

                     city     state postal_code   latitude   longitude  stars  \
0                 Boulder  Colorado       80302  40.017544 -105.283348    4.0   
1                Portland    Oregon       97218  45.588906 -122.593331    4.0   
2                Portland    Oregon       97214  45.511907 -122.613693    4.5   
3             Orange City   Florida       32763  28.914482  -81.295979    3.0   
4                 Atlanta   Georgia       30316  33.747027  -84.353424    4.0   
...                   ...       ...         ...        ...         ...    ...   
160580             Austin     Texas       78701  30.272921  -97.744386    4.0   
160581            Orlando   Florida       32833  28.499836  -81.047478    4.5   
160582            Orlando   Florida       32825  28.511615  -81.270020    5.0   
160583           Portland    Oregon       97209  45.529647 -122.685153    4.0   
160584  Altamonte Springs   Florida       32701  28.663047  -81.346728    4.5   

        review_count  is_open  \
0                 86        1   
1                126        1   
2                 13        1   
3                  8        1   
4                 14        1   
...              ...      ...   
160580             8        1   
160581            18        1   
160582             8        0   
160583            10        1   
160584            82        0   

                                               attributes  \
0       {'RestaurantsTableService': 'True', 'WiFi': 'u...   
1       {'RestaurantsTakeOut': 'True', 'RestaurantsAtt...   
2       {'BusinessAcceptsCreditCards': 'True', 'Restau...   
3       {'RestaurantsPriceRange2': '1', 'BusinessAccep...   
4       {'GoodForKids': 'False', 'BusinessParking': '{...   
...                                                   ...   
160580                                               None   
160581  {'RestaurantsTakeOut': 'True', 'RestaurantsPri...   
160582  {'DogsAllowed': 'False', 'ByAppointmentOnly': ...   
160583  {'RestaurantsTakeOut': 'True', 'RestaurantsDel...   
160584  {'RestaurantsReservations': 'True', 'OutdoorSe...   

                                               categories  \
0       Gastropubs, Food, Beer Gardens, Restaurants, B...   
1       Salad, Soup, Sandwiches, Delis, Restaurants, C...   
2       Antiques, Fashion, Used, Vintage & Consignment...   
3                              Beauty & Spas, Hair Salons   
4       Gyms, Active Life, Interval Training Gyms, Fit...   
...                                                   ...   
160580  Real Estate, Real Estate Services, Home Servic...   
160581      Health Markets, Food, Specialty Food, Grocery   
160582  Arts & Entertainment, Paint & Sip, Art Classes...   
160583              Cuban, Sandwiches, Restaurants, Cafes   
160584  Restaurants, Middle Eastern, Mediterranean, Pe...   

                                                    hours     county  
0       {'Monday': '11:0-23:0', 'Tuesday': '11:0-23:0'...    Boulder  
1       {'Monday': '5:0-18:0', 'Tuesday': '5:0-17:0', ...  Multnomah

In [63]:
business

business_id                     name               address  \
0       6iYb2HFDywm3zjuRg0shjw      Oskar Blues Taproom          921 Pearl St   
1       tCbdrRPZA0oiIYSmHG3J0w  Flying Elephants at PDX   7000 NE Airport Way   
2       bvN78flM8NLprQ1a1y5dRg           The Reclaimory    4720 Hawthorne Ave   
3       oaepsyvc0J17qwi8cfrOWg              Great Clips    2566 Enterprise Rd   
4       PE9uqAjdw0E4-8mjGl3wVA        Crossfit Terminus   1046 Memorial Dr SE   
...                        ...                      ...                   ...   
160580  D2mHoIDXx9N8mS1pGoKV9Q       Eleven Oaks Realty                         
160581  bQX-kwVTyZgcdZGEPzce6Q             Webb's Honey    21777 State Rd 520   
160582  wvFZ06nmPmQ2-IVoPqVYLA    Painting with a Twist  2164 S Chickasaw Trl   
160583  GB75wPibj3IjNauaoCxyGA              Havana Cafe        910 NW 14th St   
160584  ngmLL5Y5OT-bYHKU0kKrYA              Zora Grille   1370 E Altamonte Dr   

                     city     state postal_code   latitude   longitude  stars  \
0                 Boulder  Colorado       80302  40.017544 -105.283348    4.0   
1                Portland    Oregon       97218  45.588906 -122.593331    4.0   
2                Portland    Oregon       97214  45.511907 -122.613693    4.5   
3             Orange City   Florida       32763  28.914482  -81.295979    3.0   
4                 Atlanta   Georgia       30316  33.747027  -84.353424    4.0   
...                   ...       ...         ...        ...         ...    ...   
160580             Austin     Texas       78701  30.272921  -97.744386    4.0   
160581            Orlando   Florida       32833  28.499836  -81.047478    4.5   
160582            Orlando   Florida       32825  28.511615  -81.270020    5.0   
160583           Portland    Oregon       97209  45.529647 -122.685153    4.0   
160584  Altamonte Springs   Florida       32701  28.663047  -81.346728    4.5   

        review_count  is_open  \
0                 86        1   
1                126        1   
2                 13        1   
3                  8        1   
4                 14        1   
...              ...      ...   
160580             8        1   
160581            18        1   
160582             8        0   
160583            10        1   
160584            82        0   

                                               attributes  \
0       {'RestaurantsTableService': 'True', 'WiFi': 'u...   
1       {'RestaurantsTakeOut': 'True', 'RestaurantsAtt...   
2       {'BusinessAcceptsCreditCards': 'True', 'Restau...   
3       {'RestaurantsPriceRange2': '1', 'BusinessAccep...   
4       {'GoodForKids': 'False', 'BusinessParking': '{...   
...                                                   ...   
160580                                               None   
160581  {'RestaurantsTakeOut': 'True', 'RestaurantsPri...   
160582  {'DogsAllowed': 'False', 'ByAppointmentOnly': ...   
160583  {'RestaurantsTakeOut': 'True', 'RestaurantsDel...   
160584  {'RestaurantsReservations': 'True', 'OutdoorSe...   

                                               categories  \
0       Gastropubs, Food, Beer Gardens, Restaurants, B...   
1       Salad, Soup, Sandwiches, Delis, Restaurants, C...   
2       Antiques, Fashion, Used, Vintage & Consignment...   
3                              Beauty & Spas, Hair Salons   
4       Gyms, Active Life, Interval Training Gyms, Fit...   
...                                                   ...   
160580  Real Estate, Real Estate Services, Home Servic...   
160581      Health Markets, Food, Specialty Food, Grocery   
160582  Arts & Entertainment, Paint & Sip, Art Classes...   
160583              Cuban, Sandwiches, Restaurants, Cafes   
160584  Restaurants, Middle Eastern, Mediterranean, Pe...   

                                                    hours  
0       {'Monday': '11:0-23:0', 'Tuesday': '11:0-23:0'...  
1       {'Monday': '5:0-18:0', 'Tuesday': '5:0-17:0', ...  
2       {'Thursday': '11:0-18:

In [70]:
yelpb_url = "https://media.githubusercontent.com/media/SteinsGate9/05-839-a2/main/data/business.json"
business = pd.read_json(yelpb_url, lines=True)


In [71]:
business

business_id                     name               address  \
0       6iYb2HFDywm3zjuRg0shjw      Oskar Blues Taproom          921 Pearl St   
1       tCbdrRPZA0oiIYSmHG3J0w  Flying Elephants at PDX   7000 NE Airport Way   
2       bvN78flM8NLprQ1a1y5dRg           The Reclaimory    4720 Hawthorne Ave   
3       oaepsyvc0J17qwi8cfrOWg              Great Clips    2566 Enterprise Rd   
4       PE9uqAjdw0E4-8mjGl3wVA        Crossfit Terminus   1046 Memorial Dr SE   
...                        ...                      ...                   ...   
160580  D2mHoIDXx9N8mS1pGoKV9Q       Eleven Oaks Realty                         
160581  bQX-kwVTyZgcdZGEPzce6Q             Webb's Honey    21777 State Rd 520   
160582  wvFZ06nmPmQ2-IVoPqVYLA    Painting with a Twist  2164 S Chickasaw Trl   
160583  GB75wPibj3IjNauaoCxyGA              Havana Cafe        910 NW 14th St   
160584  ngmLL5Y5OT-bYHKU0kKrYA              Zora Grille   1370 E Altamonte Dr   

                     city state postal_code   latitude   longitude  stars  \
0                 Boulder    CO       80302  40.017544 -105.283348    4.0   
1                Portland    OR       97218  45.588906 -122.593331    4.0   
2                Portland    OR       97214  45.511907 -122.613693    4.5   
3             Orange City    FL       32763  28.914482  -81.295979    3.0   
4                 Atlanta    GA       30316  33.747027  -84.353424    4.0   
...                   ...   ...         ...        ...         ...    ...   
160580             Austin    TX       78701  30.272921  -97.744386    4.0   
160581            Orlando    FL       32833  28.499836  -81.047478    4.5   
160582            Orlando    FL       32825  28.511615  -81.270020    5.0   
160583           Portland    OR       97209  45.529647 -122.685153    4.0   
160584  Altamonte Springs    FL       32701  28.663047  -81.346728    4.5   

        review_count  is_open  \
0                 86        1   
1                126        1   
2                 13        1   
3                  8        1   
4                 14        1   
...              ...      ...   
160580             8        1   
160581            18        1   
160582             8        0   
160583            10        1   
160584            82        0   

                                               attributes  \
0       {'RestaurantsTableService': 'True', 'WiFi': 'u...   
1       {'RestaurantsTakeOut': 'True', 'RestaurantsAtt...   
2       {'BusinessAcceptsCreditCards': 'True', 'Restau...   
3       {'RestaurantsPriceRange2': '1', 'BusinessAccep...   
4       {'GoodForKids': 'False', 'BusinessParking': '{...   
...                                                   ...   
160580                                               None   
160581  {'RestaurantsTakeOut': 'True', 'RestaurantsPri...   
160582  {'DogsAllowed': 'False', 'ByAppointmentOnly': ...   
160583  {'RestaurantsTakeOut': 'True', 'RestaurantsDel...   
160584  {'RestaurantsReservations': 'True', 'OutdoorSe...   

                                               categories  \
0       Gastropubs, Food, Beer Gardens, Restaurants, B...   
1       Salad, Soup, Sandwiches, Delis, Restaurants, C...   
2       Antiques, Fashion, Used, Vintage & Consignment...   
3                              Beauty & Spas, Hair Salons   
4       Gyms, Active Life, Interval Training Gyms, Fit...   
...                                                   ...   
160580  Real Estate, Real Estate Services, Home Servic...   
160581      Health Markets, Food, Specialty Food, Grocery   
160582  Arts & Entertainment, Paint & Sip, Art Classes...   
160583              Cuban, Sandwiches, Restaurants, Cafes   
160584  Restaurants, Middle Eastern, Mediterranean, Pe...   

                                                    hours  
0       {'Monday': '11:0-23:0', 'Tuesday': '11:0-23:0'...  
1       {'Monday': '5:0-18:0', 'Tuesday': '5:0-17:0', ...  
2       {'Thursday': '11:0-18:0', 'Friday': '11:0-18:0...  
3                 

In [1]:
import gdown
url = 'https://drive.google.com/file/d/14rU2Gs6RkRJ_hHqIhW-EWJXjuMVkDHkE'
output = 'check.csv'
gdown.download(url, output, quiet=False)

ModuleNotFoundError: No module named 'gdown'

In [90]:
import pandas as pd

url = 'https://drive.google.com/file/d/14rU2Gs6RkRJ_hHqIhW-EWJXjuMVkDHkE/view?usp=sharing'
path = 'https://drive.google.com/uc?export=download&id='+url.split('/')[-2]
print(path)
df = pd.read_csv(path)

https://drive.google.com/uc?export=download&id=14rU2Gs6RkRJ_hHqIhW-EWJXjuMVkDHkE


URLError: <urlopen error [Errno 0] Error>

In [4]:
business_state = pd.read_csv("https://media.githubusercontent.com/media/SteinsGate9/assignemnt2/master/data/business_state.csv")
business_county = pd.read_csv("https://media.githubusercontent.com/media/SteinsGate9/assignemnt2/master/data/business_county.csv")
business_state_forshow = pd.read_csv("https://media.githubusercontent.com/media/SteinsGate9/assignemnt2/master/data/business_state_forshow.csv")
business_county_forshow = pd.read_csv("https://media.githubusercontent.com/media/SteinsGate9/assignemnt2/master/data/business_county_forshow.csv")


NameError: name 'pd' is not defined